In [ ]:
import pandas as pd
import numpy as np
from collections import Counter
from collections import defaultdict
from typing import List, Dict, Tuple
from mlxtend.frequent_patterns import apriori, association_rules
from mlxtend.preprocessing import TransactionEncoder
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
df = pd.read_excel('/content/drive/MyDrive/Fall 2024/Data Mining/homework/Shopping Basket Database.xlsx')


df.head(5)

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


Unnamed: 0  Store  Shopper  \
0           0     45   629346   
1           1     47   845850   
2           2     37   730158   
3           3     10   672217   
4           4      6   717595   

                                              Basket  
0  tomatoes, salsa, limes, vinegar, toothpaste, h...  
1    sunscreen, salmon, garlic, salsa, lotion, yeast  
2  lemons, ham, beef, lotion, paprika, corn, pita...  
3  apples, potatoes, onions, mustard, tomatoes, m...  
4  ham, bleach, sugar, apples, bread, buns, mayo,...

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50000 entries, 0 to 49999
Data columns (total 4 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   Unnamed: 0  50000 non-null  int64 
 1   Store       50000 non-null  int64 
 2   Shopper     50000 non-null  int64 
 3   Basket      50000 non-null  object
dtypes: int64(3), object(1)
memory usage: 1.5+ MB


/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [ ]:
df.drop('Unnamed: 0', axis=1, inplace=True)


/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50000 entries, 0 to 49999
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   Store    50000 non-null  int64 
 1   Shopper  50000 non-null  int64 
 2   Basket   50000 non-null  object
dtypes: int64(2), object(1)
memory usage: 1.1+ MB


/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [ ]:
def clean_and_analyze_baskets(df):

    # Create a copy to avoid modifying original
    df_clean = df.copy()

    # Clean the Basket column
    df_clean['Basket'] = df_clean['Basket'].str.strip()

    # Convert basket strings to lists of items
    df_clean['Basket_List'] = df_clean['Basket'].str.split(',\s*')

    # Basic statistics
    stats = {
        'total_transactions': len(df_clean),
        'unique_stores': df_clean['Store'].nunique(),
        'unique_shoppers': df_clean['Shopper'].nunique(),
        'transactions_per_store': df_clean.groupby('Store').size().describe().to_dict(),
    }

    # Get all unique items and their frequencies
    all_items = [item for basket in df_clean['Basket_List'] for item in basket]
    item_frequencies = Counter(all_items)

    # Find top selling items
    top_items = pd.DataFrame.from_dict(item_frequencies, orient='index',
                                     columns=['frequency']).sort_values('frequency',
                                     ascending=False)

    # Store statistics per store
    store_stats = df_clean.groupby('Store').agg({
         # Number of transactions
        'Shopper': 'count',
         # Total items sold
        'Basket_List': lambda x: sum(len(basket) for basket in x)
    }).rename(columns={
        'Shopper': 'transaction_count',
        'Basket_List': 'total_items_sold'
    })

    return df_clean, stats, top_items, store_stats

# Clean and analyze the data
df_cleaned, dataset_stats, top_selling_items, store_statistics = clean_and_analyze_baskets(df)


print("\nTop 10 Selling Items:")
print(top_selling_items.head(10))

print("\nStore Transaction Statistics:")
print(store_statistics.describe())

# Check for any potential data quality issues
print("\nData Quality Checks:")
print(f"Empty baskets: {df_cleaned['Basket_List'].apply(len).eq(0).sum()}")
print(f"Average items per basket: {df_cleaned['Basket_List'].apply(len).mean():.2f}")

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
<>:10: DeprecationWarning: invalid escape sequence '\s'
<>:10: DeprecationWarning: invalid escape sequence '\s'
<ipython-input-116-7ee46f9daee1>:10: DeprecationWarning: invalid escape sequence '\s'
  df_clean['Basket_List'] = df_clean['Basket'].str.split(',\s*')



Top 10 Selling Items:
           frequency
apples         22625
foil           15277
coffee         14452
buns           14210
tuna           13784
ham            12348
diapers        12207
mayo           12198
tortillas      12057
soap           12056

Store Transaction Statistics:
       transaction_count  total_items_sold
count          50.000000         50.000000
mean         1000.000000      11408.200000
std            27.732689        349.507992
min           936.000000      10676.000000
25%           985.000000      11167.250000
50%           998.000000      11386.500000
75%          1019.500000      11678.500000
max          1062.000000      12134.000000

Data Quality Checks:
Empty baskets: 0
Average items per basket: 11.41


In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50000 entries, 0 to 49999
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   Store    50000 non-null  int64 
 1   Shopper  50000 non-null  int64 
 2   Basket   50000 non-null  object
dtypes: int64(2), object(1)
memory usage: 1.1+ MB


/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [ ]:
class PCY:
    def __init__(self, min_support: float, num_buckets: int = 50000):
        self.min_support = min_support
        self.num_buckets = num_buckets
        self.n_transactions = 0
        self.item_counts = defaultdict(int)
        self.bucket_counts = defaultdict(int)
        self.bitmap = set()
        self.frequent_items = set()
        self.frequent_pairs = []
        self.frequent_triplets = []

    def _hash_pair(self, item1: str, item2: str) -> int:
        return hash(f"{item1},{item2}") % self.num_buckets

    def first_pass(self, transactions: List[List[str]]):
        self.n_transactions = len(transactions)
        min_count = self.min_support * self.n_transactions

        for basket in transactions:
            for item in basket:
                self.item_counts[item] += 1

            for i in range(len(basket)):
                for j in range(i + 1, len(basket)):
                    bucket = self._hash_pair(basket[i], basket[j])
                    self.bucket_counts[bucket] += 1

        self.frequent_items = {item for item, count in self.item_counts.items() if count >= min_count}
        min_bucket_count = self.min_support * self.n_transactions
        self.bitmap = {bucket for bucket, count in self.bucket_counts.items() if count >= min_bucket_count}
        self.bucket_counts.clear()

    def second_pass(self, transactions: List[List[str]]):
        pair_counts = defaultdict(int)
        min_count = self.min_support * self.n_transactions

        for basket in transactions:
            freq_items_in_basket = [item for item in basket if item in self.frequent_items]
            for i in range(len(freq_items_in_basket)):
                for j in range(i + 1, len(freq_items_in_basket)):
                    item1, item2 = freq_items_in_basket[i], freq_items_in_basket[j]
                    bucket = self._hash_pair(item1, item2)

                    if bucket in self.bitmap:
                        pair = tuple(sorted([item1, item2]))
                        pair_counts[pair] += 1

        self.frequent_pairs = [(pair, count) for pair, count in pair_counts.items() if count >= min_count]

    def third_pass(self, transactions: List[List[str]]):
        triplet_counts = defaultdict(int)
        min_count = self.min_support * self.n_transactions

        for basket in transactions:
            freq_items_in_basket = [item for item in basket if item in self.frequent_items]
            for i in range(len(freq_items_in_basket)):
                for j in range(i + 1, len(freq_items_in_basket)):
                    for k in range(j + 1, len(freq_items_in_basket)):
                        triplet = tuple(sorted([freq_items_in_basket[i], freq_items_in_basket[j], freq_items_in_basket[k]]))
                        triplet_counts[triplet] += 1

        self.frequent_triplets = [(triplet, count) for triplet, count in triplet_counts.items() if count >= min_count]

    def fit(self, df: pd.DataFrame, basket_col: str = 'Basket'):
        if isinstance(df[basket_col].iloc[0], str):
            transactions = df[basket_col].str.split().tolist()
        else:
            transactions = df[basket_col].tolist()

        transactions = [[item.strip().rstrip(',') for item in transaction] for transaction in transactions]
        print("Cleaned Transactions:", transactions)

        self.first_pass(transactions)
        print("Frequent Items after first pass:", self.frequent_items)
        self.second_pass(transactions)
        print("Frequent Pairs after second pass:", self.frequent_pairs)
        self.third_pass(transactions)
        print("Frequent Triplets after third pass:", self.frequent_triplets)

        return self

    def get_rules(self, min_confidence: float = 0.3) -> pd.DataFrame:
        rules = []

        for (item1, item2, item3), support_count in self.frequent_triplets:
            support = support_count / self.n_transactions
            conf_12_to_3 = support_count / self.item_counts[item3] if self.item_counts[item3] > 0 else 0
            conf_13_to_2 = support_count / self.item_counts[item2] if self.item_counts[item2] > 0 else 0
            conf_23_to_1 = support_count / self.item_counts[item1] if self.item_counts[item1] > 0 else 0

            if conf_12_to_3 >= min_confidence:
                rules.append({'antecedent': (item1, item2), 'consequent': item3, 'support': support, 'confidence': conf_12_to_3, 'rule': f"({item1}, {item2}) -> {item3}"})
            if conf_13_to_2 >= min_confidence:
                rules.append({'antecedent': (item1, item3), 'consequent': item2, 'support': support, 'confidence': conf_13_to_2, 'rule': f"({item1}, {item3}) -> {item2}"})
            if conf_23_to_1 >= min_confidence:
                rules.append({'antecedent': (item2, item3), 'consequent': item1, 'support': support, 'confidence': conf_23_to_1, 'rule': f"({item2}, {item3}) -> {item1}"})

        rules_df = pd.DataFrame(rules)
        if not rules_df.empty:
            rules_df = rules_df.sort_values(['confidence'], ascending=[False])

        return rules_df

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [ ]:
# Initialize and run PCY
pcy = PCY(min_support=0.2, num_buckets=500)
pcy.fit(df)
rules_df = pcy.get_rules(min_confidence=0.3)

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


Cleaned Transactions: [['tomatoes', 'salsa', 'limes', 'vinegar', 'toothpaste', 'honey', 'soap', 'mayo', 'chicken'], ['sunscreen', 'salmon', 'garlic', 'salsa', 'lotion', 'yeast'], ['lemons', 'ham', 'beef', 'lotion', 'paprika', 'corn', 'pita', 'cinamon', 'soap', 'onions', 'yeast', 'coffee', 'buns', 'bleach', 'tomatoes', 'bread', 'batteries', 'mayo'], ['apples', 'potatoes', 'onions', 'mustard', 'tomatoes', 'mayo', 'strawberries', 'cinamon', 'diapers', 'beef'], ['ham', 'bleach', 'sugar', 'apples', 'bread', 'buns', 'mayo', 'limes', 'cinamon'], ['coffee', 'eggs', 'salmon', 'limes', 'detergent', 'flour', 'peaches', 'pasta', 'ham', 'foil', 'apples', 'tortillas', 'tuna', 'diapers', 'jelly'], ['salsa', 'shrimp', 'tortillas', 'tuna', 'bleach', 'bacon'], ['apples', 'beef', 'yogurt', 'tuna', 'soap', 'cookies', 'bleach', 'foil', 'garlic', 'mouthwash', 'milk', 'mayo', 'salmon', 'carrots', 'sugar'], ['mouthwash', 'beans', 'apples', 'feta', 'salmon', 'bananas', 'pasta', 'tomatoes', 'yeast'], ['diapers'

In [ ]:
# Compute the total number of transactions per store
df['total_transactions'] = df.groupby('Store')['Shopper'].transform('count')

# Compute the total number of items sold per store
df['total_items_sold'] = df.groupby('Store')['Basket'].transform(lambda x: sum(len(str(b).split(',')) for b in x))

# Standardize the features
scaler = StandardScaler()
X = scaler.fit_transform(df[['total_transactions', 'total_items_sold']])

# Perform k-means clustering
kmeans = KMeans(n_clusters=2, init='random', n_init=10, random_state=42)
kmeans.fit(X)

# Get the cluster labels and centroids
labels = kmeans.labels_
centroids = kmeans.cluster_centers_

# Print the cluster labels for each store
print("Cluster Labels:")
print(df['Store'].to_frame().assign(cluster=labels))

# Print the cluster centroids
print("\nCluster Centroids:")
print(pd.DataFrame(centroids, columns=['total_transactions', 'total_items_sold']))

Cluster Labels:
       Store  cluster
0         45        0
1         47        0
2         37        0
3         10        1
4          6        0
...      ...      ...
49995     35        0
49996     46        1
49997     16        0
49998     48        1
49999     46        1

[50000 rows x 2 columns]

Cluster Centroids:
   total_transactions  total_items_sold
0            0.713731          0.736139
1           -0.875233         -0.902712


/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
